In [1]:
from __future__ import print_function
from pyspark.ml.feature import HashingTF, IDF, Tokenizer, StopWordsRemover
from pyspark import SparkContext, SparkConf
from pyspark.sql.session import SparkSession
from pyspark.sql.types import *
from pyspark.sql.functions import array, struct, split, explode, udf
from pyspark.sql import functions as f

In [2]:
conf = SparkConf().setMaster("local[*]").setAppName('haha')
sc = SparkContext(conf=conf)
spark = SparkSession(sc)

In [6]:
spark.read.json('reviews_Books_5.json').printSchema()

root
 |-- asin: string (nullable = true)
 |-- helpful: array (nullable = true)
 |    |-- element: long (containsNull = true)
 |-- overall: double (nullable = true)
 |-- reviewText: string (nullable = true)
 |-- reviewTime: string (nullable = true)
 |-- reviewerID: string (nullable = true)
 |-- reviewerName: string (nullable = true)
 |-- summary: string (nullable = true)
 |-- unixReviewTime: long (nullable = true)



In [3]:
review_sp = spark.read.json('reviews_Books_5.json').select("asin","reviewText")
review_sp.show(5)

+----------+--------------------+
|      asin|          reviewText|
+----------+--------------------+
|000100039X|Spiritually and m...|
|000100039X|This is one my mu...|
|000100039X|This book provide...|
|000100039X|I first read THE ...|
|000100039X|A timeless classi...|
+----------+--------------------+
only showing top 5 rows



In [8]:
# group by asin, all reviewText will be in the same row
reviews = review_sp.groupBy("asin").agg(f.concat_ws(" ", f.collect_list('reviewText')).alias('reviewText'))
reviews.show(5)

+----------+--------------------+
|      asin|          reviewText|
+----------+--------------------+
|0001837192|At least it was f...|
|0001845357|Last year I track...|
|0002216973|And to me, there'...|
|000255111X|This is what Joyc...|
|0004708075|Seller's contact ...|
+----------+--------------------+
only showing top 5 rows



In [9]:
tokenizer = Tokenizer(inputCol="reviewText", outputCol="words")
reviews_w_words = tokenizer.transform(reviews)
remover = StopWordsRemover(inputCol="words", outputCol="mf_words")
reviews_w_mfwords = remover.transform(reviews_w_words)
reviews_w_mfwords.show(3)

+----------+--------------------+--------------------+--------------------+
|      asin|          reviewText|               words|            mf_words|
+----------+--------------------+--------------------+--------------------+
|0001837192|At least it was f...|[at, least, it, w...|[least, first, re...|
|0001845357|Last year I track...|[last, year, i, t...|[last, year, trac...|
|0002216973|And to me, there'...|[and, to, me,, th...|[me,, big, differ...|
+----------+--------------------+--------------------+--------------------+
only showing top 3 rows



In [10]:
hashingTF = HashingTF(inputCol="mf_words", outputCol="tf", numFeatures=20)
tf = hashingTF.transform(reviews_w_mfwords)
idf = IDF(inputCol="tf", outputCol="tfidf").fit(tf)
tfidf = idf.transform(tf)
for item in tfidf.select('tfidf').collect():
    print(item)

Row(tfidf=SparseVector(20, {0: 0.3468, 1: 0.0821, 2: 0.102, 3: 0.39, 5: 0.2963, 6: 0.4629, 7: 0.3738, 8: 0.4346, 10: 0.1704, 11: 0.1775, 12: 0.1267, 13: 0.1834, 14: 0.1719, 15: 0.1323, 16: 0.0872, 17: 0.3081, 18: 0.3184, 19: 0.3562}))
Row(tfidf=SparseVector(20, {0: 1.4863, 1: 2.3804, 2: 1.9373, 3: 1.8719, 4: 1.179, 5: 1.7776, 6: 1.9289, 7: 1.6822, 8: 2.0489, 9: 1.8532, 10: 1.8174, 11: 1.5978, 12: 1.1826, 13: 0.8252, 14: 2.2343, 15: 1.9183, 16: 2.4422, 17: 1.4173, 18: 1.5124, 19: 1.7097}))
Row(tfidf=SparseVector(20, {0: 4.657, 1: 4.6788, 2: 6.9337, 3: 5.2256, 4: 4.7161, 5: 4.7403, 6: 7.0984, 7: 4.0186, 8: 6.3329, 9: 5.0791, 10: 5.793, 11: 7.19, 12: 5.8287, 13: 2.5978, 14: 7.2184, 15: 4.9612, 16: 6.1054, 17: 4.4368, 18: 4.4575, 19: 7.0527}))
Row(tfidf=SparseVector(20, {0: 0.4459, 1: 0.3283, 2: 0.102, 3: 1.2479, 4: 0.7205, 5: 0.3703, 6: 0.6173, 7: 0.3738, 8: 0.8071, 9: 0.3432, 10: 0.7383, 11: 0.7989, 12: 0.9715, 13: 0.3362, 14: 0.7734, 15: 0.7276, 16: 0.6105, 17: 0.6778, 18: 0.398, 19: 0.

Row(tfidf=SparseVector(20, {0: 1.5853, 1: 1.3954, 2: 1.4275, 3: 1.2479, 4: 1.3755, 5: 1.3332, 6: 2.0832, 7: 1.2149, 8: 2.4214, 9: 1.0295, 10: 1.0791, 11: 1.4203, 12: 1.4783, 13: 0.7335, 14: 1.7187, 15: 1.2568, 16: 0.9594, 17: 1.0476, 18: 1.5124, 19: 1.8522}))
Row(tfidf=SparseVector(20, {0: 0.0495, 1: 0.0821, 4: 0.0655, 5: 0.0741, 7: 0.2804, 8: 0.0621, 10: 0.0568, 13: 0.0306, 17: 0.0616, 18: 0.0796, 19: 0.0712}))
Row(tfidf=SparseVector(20, {0: 1.2881, 1: 2.0521, 2: 1.8354, 3: 1.6379, 4: 1.965, 5: 1.9998, 6: 1.7746, 7: 1.4018, 8: 1.0555, 9: 1.8532, 10: 1.363, 11: 0.8877, 12: 2.0696, 13: 0.9169, 14: 1.0312, 15: 1.9845, 16: 1.8316, 17: 1.7254, 18: 1.194, 19: 1.2111}))
Row(tfidf=SparseVector(20, {0: 0.0991, 2: 0.4079, 3: 0.234, 4: 0.3275, 6: 0.1543, 7: 0.3738, 8: 0.2484, 9: 0.2745, 10: 0.1704, 11: 0.3551, 13: 0.2139, 14: 0.1719, 15: 0.1984, 16: 0.3489, 17: 0.0616, 18: 0.2388, 19: 0.5699}))
Row(tfidf=SparseVector(20, {0: 0.2973, 1: 0.2463, 2: 0.2039, 3: 0.546, 4: 0.262, 5: 0.4444, 6: 0.1543,

Row(tfidf=SparseVector(20, {0: 1.9321, 1: 2.7909, 2: 3.1609, 3: 2.4958, 4: 1.834, 5: 1.8517, 6: 3.3949, 7: 2.7102, 8: 1.9247, 9: 1.5786, 10: 2.215, 11: 2.4854, 12: 1.1404, 13: 1.2225, 14: 2.6639, 15: 2.3814, 16: 2.6166, 17: 2.7113, 18: 2.0696, 19: 2.2084}))
Row(tfidf=SparseVector(20, {0: 27.5454, 1: 34.0649, 2: 38.4411, 3: 36.2674, 4: 41.1345, 5: 34.515, 6: 39.2727, 7: 38.4099, 8: 30.7955, 9: 30.8178, 10: 31.5773, 11: 31.2455, 12: 35.8172, 13: 17.7871, 14: 34.3733, 15: 32.6113, 16: 59.7455, 17: 37.4043, 18: 34.6256, 19: 32.4851}))
Row(tfidf=SparseVector(20, {0: 0.1486, 3: 0.234, 4: 0.262, 5: 0.0741, 6: 0.0772, 8: 0.3725, 9: 0.1373, 10: 0.3408, 11: 0.0888, 12: 0.0422, 14: 0.0859, 15: 0.1323, 16: 0.3489, 17: 0.1849, 18: 0.1592, 19: 0.3562}))
Row(tfidf=SparseVector(20, {0: 3.3193, 1: 6.2384, 2: 6.2199, 3: 5.6936, 4: 7.0741, 5: 4.8143, 6: 6.2497, 7: 6.2615, 8: 5.0912, 9: 5.6968, 10: 8.3487, 11: 4.6158, 12: 6.1244, 13: 3.5146, 14: 5.156, 15: 7.8056, 16: 7.7626, 17: 4.56, 18: 6.6863, 19: 6.9

Row(tfidf=SparseVector(20, {0: 17.4388, 1: 27.4981, 2: 34.0565, 3: 30.4178, 4: 28.0998, 5: 22.9606, 6: 29.3195, 7: 28.4102, 8: 24.5246, 9: 25.3269, 10: 27.261, 11: 33.2871, 12: 23.7796, 13: 13.9363, 14: 35.2327, 15: 27.6502, 16: 20.9327, 17: 24.094, 18: 23.8797, 19: 24.5775}))
Row(tfidf=SparseVector(20, {0: 19.371, 1: 21.2598, 2: 21.9226, 3: 23.7883, 4: 26.1348, 5: 22.4421, 6: 33.6403, 7: 23.1768, 8: 23.1587, 9: 23.5424, 10: 23.1718, 11: 24.233, 12: 15.1632, 13: 11.6136, 14: 21.4833, 15: 27.7825, 16: 20.8455, 17: 21.6292, 18: 19.3426, 19: 21.443}))
Row(tfidf=SparseVector(20, {0: 0.4954, 1: 0.4104, 2: 0.4079, 3: 0.8579, 4: 0.3275, 5: 0.0741, 6: 0.7716, 7: 0.4673, 8: 0.2484, 9: 0.3432, 10: 0.7383, 11: 0.3551, 12: 0.1689, 13: 0.2751, 14: 0.1719, 15: 0.1323, 16: 0.2617, 17: 0.7395, 18: 0.4776, 19: 0.4274}))
Row(tfidf=SparseVector(20, {0: 0.0991, 5: 0.1481, 7: 0.1869, 10: 0.0568, 11: 0.0888, 12: 0.0422, 13: 0.0611, 19: 0.1425}))
Row(tfidf=SparseVector(20, {0: 1.189, 1: 3.8579, 2: 2.1413, 3:

Row(tfidf=SparseVector(20, {0: 7.0845, 1: 5.828, 2: 8.0553, 3: 5.6156, 4: 7.9256, 5: 7.1104, 6: 9.1816, 7: 6.7287, 8: 6.4571, 9: 6.795, 10: 8.9734, 11: 6.5687, 12: 8.2785, 13: 5.7151, 14: 7.1325, 15: 10.1869, 16: 8.8092, 17: 6.84, 18: 7.2435, 19: 8.9761}))
Row(tfidf=SparseVector(20, {0: 14.5158, 1: 13.1334, 2: 14.989, 3: 15.8329, 4: 16.1132, 5: 15.7762, 6: 19.9835, 7: 15.7004, 8: 13.5351, 9: 13.59, 10: 15.959, 11: 18.6408, 12: 11.1929, 13: 10.3911, 14: 17.2726, 15: 17.5956, 16: 14.8274, 17: 12.8789, 18: 14.5666, 19: 16.1001}))
Row(tfidf=SparseVector(20, {0: 0.644, 1: 1.8058, 2: 2.0393, 3: 1.4819, 4: 1.2445, 5: 2.222, 6: 1.3117, 7: 3.1775, 8: 1.1797, 9: 1.51, 10: 1.2495, 11: 1.4203, 12: 0.5913, 13: 0.7641, 14: 1.8905, 15: 1.0584, 16: 1.1339, 17: 0.9243, 18: 1.194, 19: 1.3535}))
Row(tfidf=SparseVector(20, {0: 6.1928, 1: 5.5817, 2: 6.2199, 3: 7.7994, 4: 6.5501, 5: 4.7403, 6: 10.4161, 7: 4.5793, 8: 8.8785, 9: 5.4909, 10: 9.9389, 11: 6.6574, 12: 7.7717, 13: 3.1785, 14: 5.7575, 15: 6.681, 16

...

Row(tfidf=SparseVector(20, {0: 0.644, 1: 1.3133, 2: 0.8157, 3: 0.156, 4: 0.524, 5: 0.8147, 6: 0.7716, 7: 0.3738, 8: 0.4967, 9: 0.5491, 10: 0.284, 11: 0.7989, 12: 1.3094, 13: 0.3056, 14: 0.2578, 15: 0.5292, 16: 0.6105, 17: 0.5546, 18: 0.398, 19: 0.4274}))
Row(tfidf=SparseVector(20, {0: 0.0495, 1: 0.0821, 2: 0.2039, 3: 0.234, 4: 0.1965, 5: 0.2963, 6: 0.1543, 7: 0.0935, 11: 0.1775, 12: 0.1267, 13: 0.0917, 15: 0.1323, 17: 0.1232, 18: 0.0796, 19: 0.0712}))
Row(tfidf=SparseVector(20, {0: 1.4863, 1: 1.3133, 2: 1.3256, 3: 1.4819, 4: 1.441, 5: 1.4813, 6: 1.6203, 7: 1.4953, 8: 1.4901, 9: 1.5786, 10: 1.8174, 11: 1.6865, 12: 0.5913, 13: 0.6112, 14: 1.8905, 15: 1.4553, 16: 2.5294, 17: 1.6022, 18: 1.7512, 19: 1.2111}))
Row(tfidf=SparseVector(20, {0: 0.2973, 1: 0.1642, 2: 0.2039, 3: 0.468, 4: 0.3275, 5: 0.3703, 6: 0.5401, 7: 0.5607, 8: 0.3725, 9: 0.4805, 10: 0.3976, 11: 0.2663, 12: 1.0982, 13: 0.4584, 14: 0.7734, 15: 0.5953, 16: 0.3489, 17: 0.4314, 18: 0.9552, 19: 0.4987}))
Row(tfidf=SparseVector(20,

Row(tfidf=SparseVector(20, {0: 0.6936, 1: 0.4925, 2: 0.4079, 3: 0.7019, 4: 0.8515, 5: 0.7407, 6: 1.003, 7: 0.9345, 8: 0.8071, 9: 0.6177, 10: 0.3408, 11: 0.7101, 12: 0.6758, 13: 0.5807, 14: 1.1171, 15: 0.6615, 16: 1.6572, 17: 1.1092, 18: 0.398, 19: 0.7124}))
Row(tfidf=SparseVector(20, {3: 0.156, 4: 0.0655, 6: 0.0772, 9: 0.1373, 10: 0.0568, 12: 0.1267, 13: 0.0611, 15: 0.1323, 16: 0.0872, 17: 0.1849, 18: 0.0796, 19: 0.0712}))
Row(tfidf=SparseVector(20, {0: 0.3963, 1: 0.6567, 2: 0.2039, 3: 0.39, 4: 0.4585, 5: 0.2963, 6: 0.3086, 7: 0.6542, 8: 0.2484, 9: 0.4805, 10: 0.6247, 11: 0.4438, 12: 0.887, 13: 0.2445, 14: 0.4297, 15: 0.6615, 16: 0.785, 17: 0.1849, 18: 0.0796, 19: 0.2137}))
Row(tfidf=SparseVector(20, {0: 0.4954, 1: 0.4104, 2: 0.9177, 3: 0.9359, 4: 0.393, 5: 0.9629, 6: 0.9259, 7: 0.5607, 8: 0.683, 9: 0.3432, 10: 0.5679, 11: 0.7101, 12: 0.718, 13: 0.5807, 14: 0.9453, 15: 0.6615, 16: 1.6572, 17: 0.4314, 18: 0.5572, 19: 0.7124}))
Row(tfidf=SparseVector(20, {0: 0.4954, 1: 0.6567, 2: 0.3059,

Row(tfidf=SparseVector(20, {0: 0.0495, 2: 0.102, 3: 0.078, 4: 0.0655, 5: 0.0741, 6: 0.0772, 7: 0.3738, 8: 0.0621, 9: 0.2745, 10: 0.1704, 12: 0.0422, 13: 0.1834, 14: 0.0859, 15: 0.0661, 16: 0.0872, 17: 0.1232, 18: 0.1592, 19: 0.1425}))
Row(tfidf=SparseVector(20, {0: 0.0991, 1: 0.1642, 2: 0.102, 3: 0.078, 4: 0.131, 6: 0.1543, 7: 0.2804, 8: 0.0621, 9: 0.2745, 10: 0.1704, 11: 0.0888, 12: 0.1689, 13: 0.2445, 14: 0.3437, 15: 0.0661, 17: 0.1849, 18: 0.1592, 19: 0.2137}))
Row(tfidf=SparseVector(20, {0: 0.5945, 1: 0.5746, 2: 0.2039, 3: 0.156, 4: 0.5895, 5: 0.5925, 6: 0.3858, 7: 0.9345, 8: 0.8692, 9: 0.6177, 10: 0.3408, 11: 0.5326, 12: 0.1689, 13: 0.4279, 14: 0.8593, 15: 0.1984, 16: 0.4361, 17: 0.1849, 18: 0.398, 19: 0.7836}))
Row(tfidf=SparseVector(20, {0: 0.0991, 4: 0.0655, 5: 0.0741, 6: 0.0772, 9: 0.0686, 13: 0.1222, 14: 0.2578, 15: 0.0661, 16: 0.0872, 18: 0.0796}))
Row(tfidf=SparseVector(20, {0: 0.0991, 2: 0.102, 5: 0.0741, 7: 0.0935, 8: 0.0621, 9: 0.0686, 10: 0.0568, 12: 0.0845, 13: 0.0611,

Row(tfidf=SparseVector(20, {2: 0.2039, 3: 0.234, 4: 0.0655, 13: 0.0611, 14: 0.0859, 15: 0.1323, 17: 0.0616, 18: 0.0796}))
Row(tfidf=SparseVector(20, {0: 8.1249, 1: 14.4468, 2: 13.6634, 3: 11.9331, 4: 16.1132, 5: 14.517, 6: 15.6628, 7: 16.1677, 8: 11.7346, 9: 11.6682, 10: 12.0403, 11: 13.5811, 12: 10.4326, 13: 7.61, 14: 14.0931, 15: 16.4049, 16: 16.5718, 17: 14.6043, 18: 12.6562, 19: 16.1001}))
Row(tfidf=SparseVector(20, {0: 0.5945, 1: 0.4104, 2: 0.7138, 3: 0.8579, 4: 1.31, 5: 0.8888, 6: 0.7716, 7: 1.1215, 8: 0.683, 9: 0.8236, 10: 0.7383, 11: 0.7101, 12: 0.3801, 13: 0.4584, 14: 1.1171, 15: 1.1245, 16: 0.9594, 17: 0.5546, 18: 1.3532, 19: 0.5699}))
Row(tfidf=SparseVector(20, {0: 1.4367, 1: 0.985, 2: 0.8157, 3: 1.0139, 4: 0.9825, 5: 1.0369, 6: 1.5431, 7: 0.8411, 8: 0.9934, 9: 0.9609, 10: 1.4198, 11: 2.3079, 12: 1.0982, 13: 0.6112, 14: 1.0312, 15: 1.1245, 16: 1.2211, 17: 1.6638, 18: 1.6716, 19: 1.7097}))
Row(tfidf=SparseVector(20, {0: 2.6753, 1: 3.0371, 2: 3.2629, 3: 4.5237, 4: 2.751, 5: 2.

Row(tfidf=SparseVector(20, {0: 9.958, 1: 12.1484, 2: 13.5614, 3: 13.103, 4: 13.8862, 5: 13.332, 6: 15.4313, 7: 13.2706, 8: 9.1269, 9: 11.7369, 10: 11.9835, 11: 16.1553, 12: 9.2077, 13: 6.3263, 14: 17.1867, 15: 15.6772, 16: 13.3446, 17: 17.8086, 18: 16.3178, 19: 13.108}))
Row(tfidf=SparseVector(20, {0: 24.4243, 1: 29.3861, 2: 30.8956, 3: 43.2089, 4: 29.0823, 5: 38.8849, 6: 29.7824, 7: 36.167, 8: 42.5922, 9: 32.1219, 10: 31.2933, 11: 35.5063, 12: 35.9439, 13: 25.9166, 14: 27.7565, 15: 43.0628, 16: 31.1375, 17: 37.8973, 18: 53.0925, 19: 34.4798}))
Row(tfidf=SparseVector(20, {0: 3.0221, 1: 1.8879, 2: 3.5688, 3: 4.0557, 4: 3.144, 5: 3.8515, 6: 3.0091, 7: 4.3924, 8: 2.2352, 9: 2.8141, 10: 3.2372, 11: 3.8169, 12: 2.9566, 13: 1.9254, 14: 4.5545, 15: 2.9105, 16: 3.6632, 17: 4.1286, 18: 3.9004, 19: 3.4907}))
Row(tfidf=SparseVector(20, {0: 36.9584, 1: 45.8029, 2: 64.8502, 3: 52.7242, 4: 49.9771, 5: 51.5503, 6: 55.5527, 7: 65.0445, 8: 54.4509, 9: 55.4584, 10: 82.8052, 11: 52.638, 12: 48.8685, 13: 